In [7]:
"""
The code below was developed while following the tutorial:

How to Create Interactive Climate Model Maps in Python

https://blog.plotly.com/post/182754641327/how-to-create-interactive-climate-model-maps

1) Create an CDS at https://cds.climate.copernicus.eu/
2) Go to you account page and take how to find your API key
3) Create a file $HOME/.cdapirc containing the following:
      url: {api-url}
      key: {uid}:{api-key}
   Where {api-url} = https://cds.climate.copernicus.eu/api/v2, and {uid} and {api-key}
   can by Step 2.

"""

'\nThe code below was developed while following the tutorial:\n\nHow to Create Interactive Climate Model Maps in Python\n\nhttps://blog.plotly.com/post/182754641327/how-to-create-interactive-climate-model-maps\n\n1) Create an CDS at https://cds.climate.copernicus.eu/\n2) Go to you account page and take how to find your API key\n3) Create a file $HOME/.cdapirc containing the following:\n      url: {api-url}\n      key: {uid}:{api-key}\n   Where {api-url} = https://cds.climate.copernicus.eu/api/v2, and {uid} and {api-key}\n   can by Step 2.\n\n'

In [78]:
import xarray as xr
# tutorial said import plotly.plotly as py
# but that is depreciated
import chart_studio.plotly as py
import plotly.offline as py_off
from plotly.graph_objs import *
import numpy as np
from scipy.io import netcdf
import cdsapi
from netCDF4 import Dataset


In [45]:
# This was in the tutorial but might be depreicated
# import plotly
# py.tools.set_credentials_file(username='', api_key='')

In [81]:
# Create an account at https://account.mapbox.com/
# Create '.mapbox_token' file and paste in your mapbox token
mapbox_access_token = open(".mapbox_token").read()

In [12]:
c = cdsapi.Client()

# Go to https://cds.climate.copernicus.eu/cdsapp#!/dataset/seasonal-postprocessed-single-levels?tab=form
# Select your data
# Show API request
# Copy in request below
# Change GRIB to NetCDF

c.retrieve(
    'seasonal-postprocessed-single-levels',
    {
        'format': 'netcdf',
        'originating_centre': 'ecmwf',
        'system': '5',
        'variable': 'sea_surface_temperature_anomaly',
        'product_type': 'ensemble_mean',
        'year': '2018',
        'month': '12',
        'leadtime_month': '3',
    },
    'download.netcdf')


2020-06-02 08:46:48,620 INFO Welcome to the CDS
2020-06-02 08:46:48,621 INFO Sending request to https://cds.climate.copernicus.eu/api/v2/resources/seasonal-postprocessed-single-levels
2020-06-02 08:46:48,813 INFO Request is completed
2020-06-02 08:46:48,814 INFO Downloading http://136.156.133.32/cache-compute-0009/cache/data8/adaptor.mars.external-1590964718.0856464-10310-11-e0203498-d726-469f-82f9-f1458a720de4.nc to download.netcdf (130.4K)
2020-06-02 08:46:48,983 INFO Download rate 779.1K/s


Result(content_length=133564,content_type=application/x-netcdf,location=http://136.156.133.32/cache-compute-0009/cache/data8/adaptor.mars.external-1590964718.0856464-10310-11-e0203498-d726-469f-82f9-f1458a720de4.nc)

In [ ]:
# The data doesn't seem to download itself
# Try downloading from https://cds.climate.copernicus.eu/cdsapp#!/yourrequests

In [47]:
f_path = '/home/dan/Downloads/adaptor.mars.external-1590964718.0856464-10310-11-e0203498-d726-469f-82f9-f1458a720de4.nc'
f = Dataset(f_path)
f

<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_64BIT_OFFSET data model, file format NETCDF3):
    Conventions: CF-1.6
    history: 2020-05-31 22:38:38 GMT by grib_to_netcdf-2.16.0: /opt/ecmwf/eccodes/bin/grib_to_netcdf -S param -o /cache/data8/adaptor.mars.external-1590964718.0856464-10310-11-e0203498-d726-469f-82f9-f1458a720de4.nc /cache/tmp/e0203498-d726-469f-82f9-f1458a720de4-adaptor.mars.external-1590964718.0861902-10310-3-tmp.grib
    dimensions(sizes): longitude(360), latitude(181), time(1)
    variables(dimensions): float32 longitude(longitude), float32 latitude(latitude), int32 time(time), int16 ssta(time,latitude,longitude)
    groups: 

In [48]:
f.variables.keys()

dict_keys(['longitude', 'latitude', 'time', 'ssta'])

In [49]:
ds2 = xr.open_dataset(xr.backends.NetCDF4DataStore(f))
print(ds2)
df2 = ds2.to_dataframe()
print(df2)
df2.index[0]


<xarray.Dataset>
Dimensions:    (latitude: 181, longitude: 360, time: 1)
Coordinates:
  * longitude  (longitude) float32 0.0 1.0 2.0 3.0 ... 356.0 357.0 358.0 359.0
  * latitude   (latitude) float32 90.0 89.0 88.0 87.0 ... -88.0 -89.0 -90.0
  * time       (time) datetime64[ns] 2019-02-01
Data variables:
    ssta       (time, latitude, longitude) float32 ...
Attributes:
    Conventions:  CF-1.6
    history:      2020-05-31 22:38:38 GMT by grib_to_netcdf-2.16.0: /opt/ecmw...
                                   ssta
latitude longitude time                
 90.0    0.0       2019-02-01 -0.000026
         1.0       2019-02-01 -0.000026
         2.0       2019-02-01 -0.000026
         3.0       2019-02-01 -0.000026
         4.0       2019-02-01 -0.000026
...                                 ...
-90.0    355.0     2019-02-01       NaN
         356.0     2019-02-01       NaN
         357.0     2019-02-01       NaN
         358.0     2019-02-01       NaN
         359.0     2019-02-01       NaN

[

(90.0, 0.0, Timestamp('2019-02-01 00:00:00'))

In [23]:
# Use the timestamp from above in the line below
df_sub = df2.iloc[df2.index.get_level_values('time') == '2019-02-01']
df_sub.tail()


ssta
latitude longitude time            
-90.0    355.0     2019-02-01   NaN
         356.0     2019-02-01   NaN
         357.0     2019-02-01   NaN
         358.0     2019-02-01   NaN
         359.0     2019-02-01   NaN

In [24]:
len(df_sub.index.get_level_values('longitude')), len(df_sub['ssta']) 

(65160, 65160)

In [27]:
step = 1.0
to_bin = lambda x: np.floor(x / step) * step
df_sub["latbin"] = df_sub.index.get_level_values('latitude').map(to_bin)
df_sub["lonbin"] = df_sub.index.get_level_values('longitude').map(to_bin)
# groups = df_sub.groupby(("latbin", "lonbin"))
# Newer interpreter requere [] instead of ()
groups = df_sub.groupby(["latbin", "lonbin"])

In [29]:
df_flat = df_sub.drop_duplicates(subset=['latbin', 'lonbin'])
df_flat.head()

ssta  latbin  lonbin
latitude longitude time                                
90.0     0.0       2019-02-01 -0.000026    90.0     0.0
         1.0       2019-02-01 -0.000026    90.0     1.0
         2.0       2019-02-01 -0.000026    90.0     2.0
         3.0       2019-02-01 -0.000026    90.0     3.0
         4.0       2019-02-01 -0.000026    90.0     4.0

In [30]:
len(df_flat['lonbin'])

65160

In [31]:
df_no_nan = df_flat[np.isfinite(df_flat['ssta'])]
len(df_no_nan)

43062

In [32]:
df_no_nan.tail()

ssta  latbin  lonbin
latitude longitude time                                
-78.0    321.0     2019-02-01  0.336443   -78.0   321.0
         322.0     2019-02-01  0.336443   -78.0   322.0
         323.0     2019-02-01  0.316907   -78.0   323.0
         324.0     2019-02-01  0.316907   -78.0   324.0
         325.0     2019-02-01  0.316907   -78.0   325.0

In [ ]:
#snow = df_no_nan['sfara'].values*2419200*39*10

In [33]:
df_no_nan = df_no_nan[(df_no_nan.latbin < 90.0) & (df_no_nan.latbin > -90.0)]

In [36]:
 colorscale= [[0.0, '#171c42'], [0.07692307692307693, '#263583'], [0.15384615384615385, '#1a58af'], [0.23076923076923078, '#1a7ebd'], [0.3076923076923077, '#619fbc'], [0.38461538461538464, '#9ebdc8'], [0.46153846153846156, '#d2d8dc'], [0.5384615384615384, '#e6d2cf'], [0.6153846153846154, '#daa998'], [0.6923076923076923, '#cc7b60'], [0.7692307692307693, '#b94d36'], [0.8461538461538461, '#9d2127'], [0.9230769230769231, '#6e0e24'], [1.0, '#3c0911']]

In [37]:
#colorscale = [[0, 'rgb(54, 50, 153)'], [0.35, 'rgb(17, 123, 215)'],
#                [0.5, 'rgb(37, 180, 167)'], [0.6, 'rgb(134, 191, 118)'],
#                [0.7, 'rgb(249, 210, 41)'], [1.0, 'rgb(244, 236, 21)']]

In [82]:
data = []

data.append(
    Scattermapbox(
        lon=df_no_nan['lonbin'].values,
        lat=df_no_nan['latbin'].values,
        mode='markers',
        text=df_no_nan['ssta'].values,
#         marker=Marker(
#             cmax=2.5,
#             cmin=-2.5,
#             color=df_no_nan['ssta'].values,
#             colorscale=colorscale
#         ),
        marker=dict(color=df_no_nan['ssta'].values,
                    colorscale=colorscale,
                    size=2.5,)
    )
)
        
layout = Layout(
    margin=dict(t=0,b=0,r=0,l=0),
    autosize=True,
    hovermode='closest',
    showlegend=False,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=53,
            lon=352
        ),
        pitch=0,
        zoom=0,
        style='dark'
    ),
)

In [ ]:
fig = dict(data=data, layout=layout)
# py.iplot(fig, filename='./ecmwf_sst.html')
plotly.offline.iplot(fig, filename='./ecmwf_sst.html')

In [85]:
# Results n the same as above
# Above was from tutorial
seaSurfaceTempAnomMap = Figure(data=data, layout=layout)
seaSurfaceTempAnomMap.show()

In [86]:
# create html output
seaSurfaceTempAnomMap.write_html("./SeaSurfaceTempAnomMap.html")